# Cleaning Steam Reviews and Identifying Youtubers in them

In [1]:
import pandas as pd
import regex as re

In [2]:
#import Scraped Reviews data
reviewData = pd.read_csv("ScrappedSteamReviews.csv")
reviewData

Unnamed: 0  index        games  \
0              0      0    Snakeybus   
1              1      1    Snakeybus   
2              2      2    Snakeybus   
3              3      3    Snakeybus   
4              4      4    Snakeybus   
...          ...    ...          ...   
7555        7555    205  Bloons TD 6   
7556        7556    206  Bloons TD 6   
7557        7557    207  Bloons TD 6   
7558        7558    208  Bloons TD 6   
7559        7559    209  Bloons TD 6   

                                                 review     approval  \
0     Posted: 31 December, 2019\nHave you ever wante...  Recommended   
1     Posted: 29 December, 2023\nhere to say hi to a...  Recommended   
2     Posted: 13 February, 2021\nI bought this becau...  Recommended   
3     Posted: 28 July, 2019\nIt's simple and fun for...  Recommended   
4                           Posted: 22 April, 2020\nbus  Recommended   
...                                                 ...          ...   
7555                     Posted: August 12, 2021\nMONKE  Recommended   
7556  Posted: June 22, 2023\nTHIS IS THE MOST VIOLEN...  Recommended   
7557  Posted: May 17, 2022\nYes, I'm a simp\n\nS nip...  Recommended   
7558  Posted: January 11, 2023\nBloons TD 6 is a tow...  Recommended   
7559  Posted: August 10, 2022\nUpdate, 11/26/2023: E...  Recommended   

     helpCount  ComCount  
0          376         0  
1          195         0  
2          111         2  
3           98         0  
4          199         4  
...        ...       ...  
7555       232         0  
7556       217         4  
7557       181         0  
7558        88         8  
7559        76         0  

[7560 rows x 7 columns]

Add a Dates Column

In [3]:
reviewData_w_dates = reviewData
PostedDate = []

def addyear(input_date):
    #adds 2024 to dates that don't have a year atteched to them
    return(input_date + " 2024")




#iterate through each review and remove the data at the start
for i in range(len(reviewData_w_dates['review'])):

    #set a current review variable
    current = reviewData_w_dates['review'][i]

    #create several match objects

    #match1 is dates formated dd/month
    match1 = re.search(r'Posted:\s\d{1,2} \w+', current)
    #match2 is dates formated dd/month/yyyy
    match2 = re.search(r'Posted:\s\d{1,2} \w+,\s\d{4}', current)
    #match3 is dates formated month/dd/
    match3 = re.search(r'Posted:\s\w+ \d{1,2}', current)
    #match4 is dates formated month/dd/yyyy
    match4 = re.search(r'Posted:\s\w+ \d{1,2},\s\d{4}', current)

    #match 1 and 2 have overlay 
    if match1:
        if match2: 
            PostedDate.append(match2.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = (current.replace(match2.group(), "")).lower()
        else: 
            PostedDate.append(match1.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = current.replace(addyear(match1.group()), "").lower()


    if match3:
        if match4: 
            PostedDate.append(match4.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = current.replace(match4.group(), "").lower()
        else: 
            PostedDate.append(match3.group().replace("Posted: ", ""))
            reviewData_w_dates['review'][i] = current.replace(addyear(match3.group()), "").lower()

    reviewData_w_dates['review'][i] = reviewData_w_dates['review'][i].replace("\n", " ")


reviewData_w_dates['DatePosted'] = PostedDate 

len(PostedDate)


C:\Users\afvm3\AppData\Local\Temp\ipykernel_33248\2689957790.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  reviewData_w_dates['review'][i] = (current.replace(match2.group(), "")).lower()
C:\Users\afvm3\AppData\Local\Temp\ipykernel_33248\2689957790.py:46: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  reviewData_w_dates['review'][i] = reviewData_w_dates['review'][i].replace("\n", " ")
C:\Users\afvm3\AppData\Local\Temp\ipykernel_33248\2689957790.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-do

7560

In [4]:
reviewData_w_dates_no_d = reviewData_w_dates.drop_duplicates()
len(reviewData_w_dates_no_d)

7560

### Identify Reviews with words relevent to youtube

In [5]:
game_list = pd.read_csv("GamesList.csv")

gamenames = [] 
reviews = []

#words releveant to youtube
keywords = [
    'youtube', 'youtuber', 'video', 'channel', 'subscribe', 
    'watched', 'stream', 'streamer', 'reaction', 'playthrough',
    'let\'s play', 'review', 'gameplay', 'walkthrough', 'tutorial', 
    'live stream', 'commentary', 'episode', 'highlight', 'vlog', 
    'content creator', 'subscribe', 'subscribed', 'unboxing', 'collab', 
    'featured in', 'featured on', 'reaction video', 'uploaded', 
    'livestreamed', 'clip', 'clips', 'playback', 'fan of', 
    'mentioned in', 'shared by', "suggested"
]

#create a dataframe only containing review of a singular game 
for game in game_list['title']:
    checker = (reviewData_w_dates['games'] == game)
    current_game_df = reviewData_w_dates[checker]
    current_game_df.reset_index(inplace=True)

    relevant_locs = []

    #check to see if the review contains a word from keywords
    for i in range(len(current_game_df)):
        rev = current_game_df["review"][i]
        rev_cleaned = re.sub(r'[^a-zA-Z0-9\s]', '', rev)
        tokenised = rev_cleaned.split(" ")
        #only keep reviews that are positive
        if current_game_df["approval"][i] == "Recommended":
            for w in keywords: 
                #catch any missed capitalisation in keywords
                w_lower = w.lower()
                #if one of the key words is present in the review add the review and game name to lists
                #that will be used to make a new df
                if (w in tokenised) and i not in relevant_locs:
                        relevant_locs.append(i) 
                        gamenames.append(game)
                        reviews.append(current_game_df["review"][i])
                        break

youtube_relevant_df = pd.DataFrame({'games':gamenames, 'reviews':reviews})
print(len(reviews))

1515


In [6]:
game_list = pd.read_csv("GamesList.csv")
unique_games = game_list['title']
for ug in unique_games:
    count = 0
    for g in youtube_relevant_df["games"]: 
        if g == ug: 
            count = count + 1
    if count > 0: 
        print(ug +": " + str(count))

Snakeybus: 19
Biped: 27
Worms Rumble: 12
Wobbly Life: 208
Party Animals: 24
Bloons TD Battles 2: 10
PICO PARK: 8
Perfect Heist 2: 17
Goose Goose Duck: 55
Stumble Guys: 13
Bopl Battle: 21
Crab Game: 19
The Riflemen: 9
Scribblenauts Unlimited: 25
Pit People®: 112
Duck Game: 31
ShellShock Live: 114
Worms W.M.D: 26
Ratz Instagib: 56
Cat Goes Fishing: 17
The Mean Greens - Plastic Warfare: 34
Tower Unite: 198
Clustertruck: 40
Garry's Mod: 32
Who's Your Daddy?!: 44
Human Fall Flat: 24
Happy Room: 17
Pikuniku: 19
Stick Fight: The Game: 34
Worms_Ultimate_Mayhem: 19
Overcooked! 2: 18
Project Winter: 40
Super Animal Royale: 108
Pummel Party: 13
ibb & obb: 33
Bloons TD 6: 19


In [7]:
print(len(game_list))
print((game_list['title'][15]))

37
Pit People®


In [8]:
print((youtube_relevant_df["reviews"][559]))

 early access review this game is brilliant. been waiting for this game since it was first announced. hilarious, different, and fun... what more could you ask for?


Data Inspection for analysi sof mentioned youtubers

In [12]:
for row in range(len(youtube_relevant_df)):
    if youtube_relevant_df['games'][row] == game_list['title'][36]:
        if not("suicide" in youtube_relevant_df['reviews'][row]):
            print((youtube_relevant_df['reviews'][row]))

 this is a game that completely changes based on how you play it and how long you've played it for.  at the 0 hour mark, btd6 is a cute monkey tower defense game that seems fairly straight forward. you just place down monkeys, and these colored balloons called "bloons" come that your little monkeys pop with darts. your favorite hero is quincy, because he's all you have.  at the 25 hour mark, you might have had a couple of people tell you what's "good" or "op" in the game, then you start using these towers and upgrades for all your games. however, you still have no real understanding of what's going on in the game whatsoever, fumbling around in the dark and dying randomly to rounds all of a sudden when you thought you were doing great. your favorite hero is striker jones, and certainly not for the right reasons.  at the 50 hour mark, you seem to find more towers and upgrades that seem to work or seem good. you might even start to catch on to the common "problem" rounds like 63, or start

In [11]:
Mentioned_youtubers = ["Dank Pods", "Noodle", "Dantdm", "PewDiePie", "BulletBarry", "Jacksepticeye"]